# Mapa Coropletico de Santa Cruz

Calculo estadístico de Cantidad Poblacional y viviendas de la ciudad de Santa Cruz de la Cierra. Basado en los datos recolectados en el censo del año 2012.

In [1]:
!pip install xlrd
!pip install openpyxl

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 96.5/96.5 KB 6.3 MB/s eta 0:00:00
You should consider upgrading via the '/root/venv/bin/python -m pip install --upgrade pip' command.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.0/250.0 KB 16.5 MB/s eta 0:00:00
You should consider upgrading via the '/root/venv/bin/python -m pip install --upgrade pip' command.


In [2]:
# Importar librerias necesarias
import pandas as pd
import geopandas as gpd
import folium as fl
from bs4 import BeautifulSoup


In [3]:
# Importar capa general de las UV. de la ciudad de Santa Cruz y guardarlo en un Dataframe nuevo
dfgeo = gpd.read_file("/work/DATA/geo_capa.json") 

In [4]:
# Leer Archivo Excel con los datos de las cantidades segun las UV. y guardarlos en dataframe nuevo
df_data_censo = pd.read_excel("/work/DATA/Data_Censo_SantaCruz.xlsx") 

In [5]:
# Explorar los nombres unicos, que se tiene de Ciudades
dfgeo["name"].unique()

array(['EL TORNO', 'LA GUARDIA', 'MONTERO', 'PORONGO', 'Santa Cruz',
       'COTOCA', 'WARNES'], dtype=object)

In [6]:
# Seleccionar solo los poligonos correspondiente a la ciudad de Santa Cruz de la Cierra
dfgeo_SC = dfgeo[(dfgeo["name"] == "Santa Cruz")] 



In [7]:
# Extraer el Nombre de cada UV. que se encuentra en la descripción de la Capa.

anotar_uv = []
for val in dfgeo_SC["description"]:
    valor_html = val["value"]
    soup = BeautifulSoup(valor_html,'html.parser')
    filas = soup.find_all('td')
    for fila in filas[7]:
        anotar_uv.append(fila)

In [8]:
dfgeo_SC["UV"] = anotar_uv # Crear una nueva columna con los nombres extraídos.

/shared-libs/python3.9/py/lib/python3.9/site-packages/geopandas/geodataframe.py:1472: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [9]:
df_data_censo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 499 entries, 0 to 498
Data columns (total 3 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   UV                   499 non-null    object 
 1   Q  viviendas por UV  465 non-null    float64
 2   Q personas por UV    498 non-null    float64
dtypes: float64(2), object(1)
memory usage: 11.8+ KB


In [10]:

dfgeo_SC_Censo = pd.merge(dfgeo_SC, df_data_censo,
how='inner', on='UV')

In [11]:
dfgeo_SC_Censo.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Int64Index: 417 entries, 0 to 416
Data columns (total 15 columns):
 #   Column               Non-Null Count  Dtype   
---  ------               --------------  -----   
 0   id                   417 non-null    object  
 1   name                 417 non-null    object  
 2   description          417 non-null    object  
 3   styleUrl             417 non-null    object  
 4   fill-opacity         417 non-null    int64   
 5   fill                 417 non-null    object  
 6   stroke-opacity       417 non-null    int64   
 7   stroke               417 non-null    object  
 8   stroke-width         417 non-null    int64   
 9   label-opacity        417 non-null    int64   
 10  label-color          417 non-null    object  
 11  geometry             417 non-null    geometry
 12  UV                   417 non-null    object  
 13  Q  viviendas por UV  417 non-null    float64 
 14  Q personas por UV    417 non-null    float64 
dtypes: float64(2), 

In [12]:
#Leer Archivo Excel con localización de las Zonas y guardar en un Dataframe Nuevo
df_zonas = pd.read_excel("/work/DATA/Zona_lat_lon.xlsx") 

In [13]:
df_zonas.info() # Ver informacion del dataframe

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5 entries, 0 to 4
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   ZONAS   5 non-null      object 
 1   Lat     5 non-null      float64
 2   Lon     5 non-null      float64
dtypes: float64(2), object(1)
memory usage: 248.0+ bytes


In [14]:
# Crear el mapa Coropletico segun la información procesada

m_capa = fl.Map(location=[-17.76156507089924, -63.15492715496914], zoom_start=11.5)

# Agregar el choropleth
fl.Choropleth(
    geo_data=dfgeo_SC_Censo,
    data=df_data_censo,
    columns=["UV", "Q personas por UV"],
    key_on="properties.UV",
    bins=5,
    fill_color="YlOrRd",
    fill_opacity=0.6,
    nan_fill_color="none",
    legend_name="Q personas por UV",
    highlight=True,
    name="Q. personas por UV",
    overlay=True
).add_to(m_capa)


#Agregar nombre de las zonas
nombres_dibujados = []

for i in range(0, len(df_zonas["ZONAS"])):
    temp = df_zonas.iloc[i]["ZONAS"]
    
    # Verificar si el nombre ya se dibujó previamente, si no, Dibujar el nombre corespondiente.
    if temp not in nombres_dibujados:
        nombres_dibujados.append(temp)
        
        s = "Info"
        fl.Marker(
            [df_zonas.iloc[i]["Lat"], df_zonas.iloc[i]["Lon"]], name="Nombre",
            icon=fl.DivIcon(html=f"""<div style="font-family: fantasy; color: black; font-size: 13px; font-weight: boldest;
                                white-space: nowrap;">
                                {"{}".format(temp)}</div>""",)
        ).add_to(m_capa)

# Agregar cuadro emergente personalizado con la información que se desea mostrar
layer = fl.GeoJson(
    data=dfgeo_SC_Censo,
    name="Información",
    zoom_on_click=True,
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'transparent',
        'fillOpacity': 0
    },
    highlight_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'blue',
        'fillOpacity': 0.2
    },
    
    tooltip=fl.GeoJsonTooltip(fields=["UV", "Q personas por UV", "Q  viviendas por UV"],
                              aliases=["UV:","Cantidad Personas:","Cantidad Viviendas:"],
                              labels=True,
                              sticky=False)
)
layer.add_to(m_capa)


# Agregar la capa de visión satelital
fl.TileLayer('https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}',
             name="satelital", attr='Esri World Imagery', overlay=True).add_to(m_capa)

# Agregar controles
fl.LayerControl().add_to(m_capa)

# Mostrar el mapa
m_capa

In [15]:
# Exportar el mapa Coropletico Resultante en un archivo con extención html.
m_capa.save("Result_Mapa_coropletico_UV.html") 

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=fdfa03b2-2efb-4ad2-b72b-f244f413cac3' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>